In [2]:
import torch
from diffusers import DiffusionPipeline
from pipeline_waifu import WaifuPipeline

pipe_id = "/home/recoilme/models/waifu-2b"
variant = "fp16"
pipe = WaifuPipeline.from_pretrained(
    pipe_id, 
    variant=variant,
    trust_remote_code=True
)
print(pipe)
#pipe_sd.to("cuda")

Loading pipeline components...:   0%|          | 0/5 [00:00<?, ?it/s]

WaifuPipeline {
  "_class_name": "WaifuPipeline",
  "_diffusers_version": "0.32.0.dev0",
  "_name_or_path": "/home/recoilme/models/waifu-2b",
  "scheduler": [
    "diffusers",
    "FlowMatchEulerDiscreteScheduler"
  ],
  "text_encoder": [
    "transformers",
    "XLMRobertaModel"
  ],
  "tokenizer": [
    "transformers",
    "XLMRobertaTokenizerFast"
  ],
  "transformer": [
    "diffusers",
    "SanaTransformer2DModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ]
}



In [3]:
def txt_embeds(prompt):
    max_length = 512
    select_index = [0] + list(range(-max_length + 1, 0))
    
    text_inputs = tokenizer(
        prompt,
        padding="max_length",
        max_length=max_length,
        truncation=True,
        add_special_tokens=True,
        return_tensors="pt",
    )
    text_input_ids = text_inputs.input_ids
    prompt_attention_mask = text_inputs.attention_mask
    device = "cuda"
    prompt_attention_mask = prompt_attention_mask.to(device)
    
    prompt_embeds = text_encoder(input_ids=text_input_ids.to(device), attention_mask=prompt_attention_mask)[0][:, select_index]
    #print(prompt_embeds.shape)
            #prompt_embeds = prompt_embeds[0][:, select_index]
    prompt_attention_mask = prompt_attention_mask[:, select_index]
    #print(prompt_attention_mask.shape)
    return prompt_embeds, prompt_attention_mask

In [4]:
prompt = '1girl, solo, animal ears, bow, teeth, jacket, tail, open mouth, brown hair, orange background, bowtie, orange nails, simple background, cat ears, orange eyes, blue bow, animal ear fluff, cat tail, looking at viewer, upper body, shirt, school uniform, hood, striped bow, striped, white shirt, black jacket, blue bowtie, fingernails, long sleeves, cat girl, bangs, fangs, collared shirt, striped bowtie, short hair, tongue, hoodie, sharp teeth, facial mark, claw pose'
prompt = 'A young girl with long brown hair and brown eyes is standing against a brick wall, wearing a white shirt with a black sailor collar and a black pleated skirt. She is smiling and looking directly at the viewer, with sunlight filtering through the green vines behind her'
#prompt = 'нарядная новогодняя елка, красивые игрушки, звезда сверху, огоньки, на тёмном фоне' 
prompt_embeds, prompt_attention_mask = txt_embeds(prompt)
negative_prompt_embeds, negative_prompt_attention_mask=txt_embeds("")
print(prompt_embeds.shape)

image = pipe(
    prompt = None,
    negative_prompt = None,
    use_resolution_binning = False,
    prompt_embeds=prompt_embeds,
    prompt_attention_mask= prompt_attention_mask,
    negative_prompt_embeds = negative_prompt_embeds,
    negative_prompt_attention_mask = negative_prompt_attention_mask,
    height=768,
    width=768,
    guidance_scale=4.5,
    num_inference_steps=24,
    generator=torch.Generator(device="cuda").manual_seed(42),
)[0]

for img in image:
    img.show()

NameError: name 'tokenizer' is not defined